In [1]:
import sys
sys.path.append("../Modules/")
sys.path.append("../pyFiles/")
sys.path.append("../")
import os

import pandas as pd
import numpy as np

# from configobj import ConfigObj
# from configobj import flatten_errors
# from validate import Validator
    
import logging

# from analysisParameters import loadParameters
# from loadDataE1 import loadSessionDict

#fmt = 'logging.Formatter(''%(levelname)s_%(name)s-%(funcName)s(): - %(message)s'
fmt = '%(levelname)s_%(name)s-%(funcName)s(): - %(message)s'
logging.basicConfig(level=logging.INFO, format=fmt)
logger = logging.getLogger(__name__)

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go
import os

init_notebook_mode(connected=True)


In [2]:
# sessionDict = projectTrajectories(sessionDict)
import matplotlib.pyplot as plt
%matplotlib notebook

In [3]:
import pickle

file = open('../sessionFiles.pickle', 'rb')
allSessions = pickle.load(file)
file.close()

sessionDict = allSessions[0]

In [4]:
list(sessionDict.keys())

['subID',
 'trialInfo',
 'expConfig',
 'rawExpUnity',
 'rawExpGaze',
 'processedExp',
 'rawCalibUnity',
 'rawCalibGaze',
 'processedCalib',
 'analysisParameters']

In [5]:

processedExp = sessionDict['processedExp']


In [6]:
processedExp['worldVidTimeSec'] = np.array(processedExp['pupilTimestamp'] - processedExp['pupilTimestamp'].iloc[0])
processedExp['worldVidTimeSec'].tail(10)

7926    36.867783
7927    36.871685
7928    36.871706
7929    36.877798
7930    36.881718
7931    36.882204
7932    36.885655
7933    36.889612
7934    36.892885
7935    36.893618
Name: worldVidTimeSec, dtype: float64

## Recalculate GIW using individual eye vectors

In [7]:
blNum = 2
trNumInBlock = 2

trNumAbs = list(sessionDict['trialInfo'].groupby('blockNumber').get_group(blNum)['trialNumber'])

gbData_bl_tr = sessionDict['processedExp'].groupby(['blockNumber','trialNumber']) 
gbInfo_bl_tr = sessionDict['trialInfo'].groupby(['blockNumber','trialNumber']) 

trDataGb = gbData_bl_tr.get_group( (blNum,trNumAbs[trNumInBlock]) ) 
trInfoGb = gbInfo_bl_tr.get_group( (blNum,trNumAbs[trNumInBlock]) ) 


In [8]:
list(trDataGb)

[('ballColliderRadius', ''),
 ('ballMeshRadius', ''),
 ('ballPos', 'x'),
 ('ballPos', 'y'),
 ('ballPos', 'z'),
 ('ballRot', 'x'),
 ('ballRot', 'y'),
 ('ballRot', 'z'),
 ('ballVel', 'x'),
 ('ballVel', 'y'),
 ('ballVel', 'z'),
 ('base_data', ''),
 ('blockNumber', ''),
 ('camera', 'R0C0'),
 ('camera', 'R0C1'),
 ('camera', 'R0C2'),
 ('camera', 'R0C3'),
 ('camera', 'R1C0'),
 ('camera', 'R1C1'),
 ('camera', 'R1C2'),
 ('camera', 'R1C3'),
 ('camera', 'R2C0'),
 ('camera', 'R2C1'),
 ('camera', 'R2C2'),
 ('camera', 'R2C3'),
 ('camera', 'R3C0'),
 ('camera', 'R3C1'),
 ('camera', 'R3C2'),
 ('camera', 'R3C3'),
 ('cameraPos', 'x'),
 ('cameraPos', 'y'),
 ('cameraPos', 'z'),
 ('cameraRot', 'x'),
 ('cameraRot', 'y'),
 ('cameraRot', 'z'),
 ('confidence', ''),
 ('eye-center0-3d', 'x'),
 ('eye-center0-3d', 'y'),
 ('eye-center0-3d', 'z'),
 ('eye-center1-3d', 'x'),
 ('eye-center1-3d', 'y'),
 ('eye-center1-3d', 'z'),
 ('frameTime', ''),
 ('gaze-normal0', 'x'),
 ('gaze-normal0', 'y'),
 ('gaze-normal0', 'z'),
 (

In [9]:


def filterGazeDataByConfidence(sessionDictIn):
    
    confidenceThreshold = sessionDictIn['analysisParameters']['confidenceThreshold']
    
    def setToNan(dataFrameIn, columnLev1,idx):

        columnLev2List = list(dataFrameIn[columnLev1].columns)

        for columnLev2 in columnLev2List:

            data = np.array(dataFrameIn[(columnLev1,columnLev2)],dtype=np.float64)
            data[idx] = np.nan
            dataFrameIn[(columnLev1,columnLev2)] = data

        return dataFrameIn

    idx = np.where(sessionDictIn['processedExp']['confidence'] < confidenceThreshold)
    setToNan(sessionDictIn['processedExp'], 'gaze-normal0', idx)
    setToNan(sessionDictIn['processedExp'], 'gaze-normal1', idx)
    
    idx = np.where(sessionDictIn['processedCalib']['confidence'] < confidenceThreshold)
    setToNan(sessionDictIn['processedCalib'], 'gaze-normal0', idx)
    setToNan(sessionDictIn['processedCalib'], 'gaze-normal1', idx)
    
    logger.info('Filtered sessionDict[\'processedExp\'][\'gaze-normal0\'] by confidence')
    logger.info('Filtered sessionDict[\'processedExp\'][\'gaze-normal1\'] by confidence')
    logger.info('Filtered sessionDict[\'processedCalib\'][\'gaze-normal0\'] by confidence')
    logger.info('Filtered sessionDict[\'processedCalib\'][\'gaze-normal1\'] by confidence')
    
    return sessionDictIn

In [10]:
sessionDict = filterGazeDataByConfidence(sessionDict)

# sessionDict

INFO___main__-filterGazeDataByConfidence(): - Filtered sessionDict['processedExp']['gaze-normal0'] by confidence
INFO___main__-filterGazeDataByConfidence(): - Filtered sessionDict['processedExp']['gaze-normal1'] by confidence
INFO___main__-filterGazeDataByConfidence(): - Filtered sessionDict['processedCalib']['gaze-normal0'] by confidence
INFO___main__-filterGazeDataByConfidence(): - Filtered sessionDict['processedCalib']['gaze-normal1'] by confidence


In [11]:
# gaze_normal2_xyz = np.nanmean([sessionDict['processedExp']['gaze-normal0'], sessionDict['processedExp']['gaze-normal1']],axis=0)
# np.divide(gaze_normal2_xyz,np.linalg.norm(gaze_normal2_xyz,axis=1))

def calc_gaze_Normal2(sessionDictIn):
    
    '''
    For each row, applies nanmean to gaze-normal0 and gaze-normal1 to calculate gaze-normal2.
    gaze-normal0 is normalized.
    This means that the gaze vector may switch from monocular to the binocular avg on a per-frame basis.
    '''

        
    def avgMonoGaze_ByRow(rowIn):

        def checkNans(vecIn):

            numNans = np.sum(np.isnan(np.array(vecIn,dtype=np.float64)))

            if numNans == 3:
                return True
            else: 
                return False

        if( checkNans(rowIn['gaze-normal0']) & checkNans(rowIn['gaze-normal1']) ):

            return {('gaze_normal2','x'): np.nan,('gaze_normal2','y'): np.nan,('gaze_normal2','z'): np.nan}

        else:

            xyz = np.nanmean([rowIn['gaze-normal0'], rowIn['gaze-normal1']],axis=0)
            xyz = xyz / np.linalg.norm(xyz)

            return {('gaze_normal2','x'): xyz[0],('gaze_normal2','y'): xyz[1],('gaze_normal2','z'): xyz[2]}
    
    def avgGazeForDataFrame(sessionDictIn, dataFrameKey):
        # If the column already exists, remove it and recalculate.
        if 'gaze_normal2' in sessionDictIn[dataFrameKey].columns:
            sessionDictIn[dataFrameKey].drop("gaze_normal2", axis=1, level=0,inplace=True)

        # Average per row
        dictListOut = sessionDictIn[dataFrameKey].apply(lambda row: avgMonoGaze_ByRow(row),axis=1)

        # Convert to dataframe and join with sessionDict
        dfOut = pd.DataFrame.from_records(dictListOut)
        dfOut.columns = pd.MultiIndex.from_tuples(dfOut.columns)
        sessionDictIn[dataFrameKey] = sessionDictIn[dataFrameKey].join(dfOut)
        
        return sessionDictIn
        
    
    sessionDictIn = avgGazeForDataFrame(sessionDictIn,'processedExp')
    sessionDictIn = avgGazeForDataFrame(sessionDictIn,'processedCalib')
    
    return sessionDictIn


In [12]:
sessionDict = calc_gaze_Normal2(sessionDict)


In [13]:
#####

blNum = 2
trNumInBlock = 2

trNumAbs = list(sessionDict['trialInfo'].groupby('blockNumber').get_group(blNum)['trialNumber'])

gbData_bl_tr = sessionDict['processedExp'].groupby(['blockNumber','trialNumber']) 
gbInfo_bl_tr = sessionDict['trialInfo'].groupby(['blockNumber','trialNumber']) 

trDataGb = gbData_bl_tr.get_group( (blNum,trNumAbs[trNumInBlock]) ) 
trInfoGb = gbInfo_bl_tr.get_group( (blNum,trNumAbs[trNumInBlock]) ) 

#####

rowIn = trDataGb.iloc[10]

# list(trDataGb)

In [14]:
def calcCycGIWDir(sessionDictIn):

    def calcGIW_ByRow(rowIn):
        # Grab gransformation matrix
        headTransform_4x4 = np.reshape(rowIn['camera'].values,[4,4]).T

        # Grab cyc EIH direction
        cycEyeInHead_XYZ = rowIn['gaze_normal2']

        # Add a 1 to convert to homogeneous coordinates
        cycEyeInHead_XYZW = np.hstack( [cycEyeInHead_XYZ,1])

        # Take the dot product!
        cycGIWVec_XYZW = np.dot( headTransform_4x4,cycEyeInHead_XYZW)

        # # Now, convert into a unit direction vector from the cyclopean eye in world coordinates
        # # Also, we can discard the w term
        cycGIWDir_XYZ = (cycGIWVec_XYZW[0:3]-rowIn["cameraPos"]) / np.linalg.norm((cycGIWVec_XYZW[0:3]-rowIn["cameraPos"]))

        # # You must return as a list or a tuple
        # #return list(cycGIWDir_XYZ)
        return {('cycGIWDir','x'): cycGIWDir_XYZ[0],('cycGIWDir','y'): cycGIWDir_XYZ[1],('cycGIWDir','z'): cycGIWDir_XYZ[2]}
    
    def calcGIWForDataframe(sessionDictIn, dataFrameKey):

        # If the column already exists, remove it and recalculate.    
        if 'cycGIWDir' in sessionDictIn[dataFrameKey].columns:
            sessionDictIn[dataFrameKey].drop("cycGIWDir", axis=1, level=0,inplace=True)

        # Average per row
        dictListOut = sessionDictIn[dataFrameKey].apply(lambda row: calcGIW_ByRow(row),axis=1)

        # Convert to dataframe and join with sessionDict
        dfOut = pd.DataFrame.from_records(dictListOut)
        dfOut.columns = pd.MultiIndex.from_tuples(dfOut.columns)
        sessionDictIn[dataFrameKey] = sessionDictIn[dataFrameKey].join(dfOut)
        return sessionDictIn
    
    sessionDictIn = calcGIWForDataframe(sessionDictIn, 'processedExp')
    sessionDictIn = calcGIWForDataframe(sessionDictIn, 'processedCalib')
    
    return sessionDictIn


In [15]:
sessionDict = calcCycGIWDir(sessionDict)

In [16]:
from processData import calcSphericalcoordinates
sessionDict = calcSphericalcoordinates(sessionDict) 

INFO_processData-calcSphericalcoordinates(): - Added sessionDict['processedExp']['ball_az']
INFO_processData-calcSphericalcoordinates(): - Added sessionDict['processedExp']['ball_el']
INFO_processData-calcSphericalcoordinates(): - Added sessionDict['processedExp']['cycGIW_az']
INFO_processData-calcSphericalcoordinates(): - Added sessionDict['processedExp']['cycGIW_el']


CWD:/Users/gjdpci/Documents/GitHub/Interception_UXF_Analysis/Analysis Notebooks


In [17]:
# # yLim = [-100,100]

# yLim=[-50,50]
# width=800
# height=600

# startTimeS = df2['worldVidTimeSec'].iloc[0]
# endTimeS = df2['worldVidTimeSec'].iloc[-2]

# # I googled for, "python find first larger than"
# startIndex = next(idx for idx, val in enumerate(df2['worldVidTimeSec']) if val >  startTimeS)
# endIndex = next(idx for idx, val in enumerate(df2['worldVidTimeSec']) if val >  endTimeS)
# print('Plotting from index: ' + str(startIndex) + ' to ' + str(endIndex))

# colors_idx = ['rgb(0,204,204)','rgb(128,128,128)','rgb(204,0,0)','rgb(102,0,204)', 'rgb(150,50,50)', 'rgb(50,50,150)']

# # from plotly.subplots import make_subplots
# # fig = make_subplots(rows=2, cols=1,shared_xaxes=True)

# traces = []

# ###

# bEih_el = go.Scattergl(
#     x=df2['worldVidTimeSec'][startIndex:endIndex],
#     y=df2['ball_el'][startIndex:endIndex],
#     name = 'ball_el',
#     marker_color = colors_idx[2],
#     mode='markers',
#     marker_size = 8,
#     opacity = 0.5)

# bEih_az = go.Scattergl(
#     x=df2['worldVidTimeSec'][startIndex:endIndex],
#     y=df2['ball_az'][startIndex:endIndex],
#     name = 'ball_az',
#     marker_color = colors_idx[3],
#     mode='markers',
#     marker_size = 8,
#     opacity = 0.5)


# eih_el = go.Scattergl(
#     x=df2['worldVidTimeSec'][startIndex:endIndex],
#     y=-df2['gazeInWorldCam_el'][startIndex:endIndex],
#     name = 'gazeInWorldCam_el',
#     marker_color = colors_idx[0],
#     mode='markers',
#     marker_size = 8,
#     opacity = 1)

# eih_az = go.Scattergl(
#     x=df2['worldVidTimeSec'][startIndex:endIndex],
#     y=df2['gazeInWorldCam_az'][startIndex:endIndex],
#     name = 'gazeInWorldCam_az',
#     marker_color = colors_idx[1],
#     mode='markers',
#     marker_size = 8,
#     opacity = 1)

# traces.append(eih_el)
# traces.append(eih_az)


# #####


# fromGP3D_el = go.Scattergl(
#     x=df2['worldVidTimeSec'][startIndex:endIndex],
#     y=-df2['fromGazePoint3d_el'][startIndex:endIndex],
#     name = 'fromGazePoint3d_el',
#     marker_color = colors_idx[4],
#     mode='markers',
#     marker_size = 3,
#     opacity = .5)

# fromGP3D_az = go.Scattergl(
#     x=df2['worldVidTimeSec'][startIndex:endIndex],
#     y=df2['fromGazePoint3d_az'][startIndex:endIndex],
#     name = 'fromGazePoint3d_az',
#     marker_color = colors_idx[5],
#     mode='markers',
#     marker_size = 3,
#     opacity = .5)

# traces.append(fromGP3D_el)
# traces.append(fromGP3D_az)


# layout = dict(
#     dragmode= 'pan',
#     title='Time Series with Rangeslider',
#     width=width,
#     height=height,
#     yaxis=dict(range=yLim, title='angular position (degrees)'),
#     xaxis=dict(
#         rangeslider=dict(visible=True))
# )


# fig = dict(data=traces, layout=layout)

# iplot(fig)



In [18]:
# yLim = [-100,100]
df2 = sessionDict['processedExp']
yLim=[-100,100]
width=800
height=600

startTimeS = df2['worldVidTimeSec'].iloc[0]
endTimeS = df2['worldVidTimeSec'].iloc[-2]

# I googled for, "python find first larger than"
startIndex = next(idx for idx, val in enumerate(df2['worldVidTimeSec']) if val >  startTimeS)
endIndex = next(idx for idx, val in enumerate(df2['worldVidTimeSec']) if val >  endTimeS)
print('Plotting from index: ' + str(startIndex) + ' to ' + str(endIndex))

colors_idx = ['rgb(0,204,204)','rgb(128,128,128)','rgb(204,0,0)','rgb(102,0,204)', 'rgb(150,50,50)', 'rgb(50,50,150)']

# from plotly.subplots import make_subplots
# fig = make_subplots(rows=2, cols=1,shared_xaxes=True)

traces = []

###

bEih_el = go.Scattergl(
    x=df2['worldVidTimeSec'][startIndex:endIndex],
    y=df2['ball_el'][startIndex:endIndex],
    name = 'ball_el',
    marker_color = colors_idx[2],
    mode='markers',
    marker_size = 8,
    opacity = 0.5)

bEih_az = go.Scattergl(
    x=df2['worldVidTimeSec'][startIndex:endIndex],
    y=df2['ball_az'][startIndex:endIndex],
    name = 'ball_az',
    marker_color = colors_idx[3],
    mode='markers',
    marker_size = 8,
    opacity = 0.5)


traces.append(bEih_el)
traces.append(bEih_az)


eih_el = go.Scattergl(
    x=df2['worldVidTimeSec'][startIndex:endIndex],
    y=-df2['cycGIW_el'][startIndex:endIndex],
    name = 'gazeInWorldCam_el',
    marker_color = colors_idx[0],
    mode='markers',
    marker_size = 8,
    opacity = 1)

eih_az = go.Scattergl(
    x=df2['worldVidTimeSec'][startIndex:endIndex],
    y=df2['cycGIW_az'][startIndex:endIndex],
    name = 'gazeInWorldCam_az',
    marker_color = colors_idx[1],
    mode='markers',
    marker_size = 8,
    opacity = 1)

traces.append(eih_el)
traces.append(eih_az)


#####


fromGP3D_el = go.Scattergl(
    x=df2['worldVidTimeSec'][startIndex:endIndex],
    y=-df2['cycGIW_el'][startIndex:endIndex],
    name = 'fromGazePoint3d_el',
    marker_color = colors_idx[4],
    mode='markers',
    marker_size = 3,
    opacity = .5)

fromGP3D_az = go.Scattergl(
    x=df2['worldVidTimeSec'][startIndex:endIndex],
    y=df2['cycGIW_az'][startIndex:endIndex],
    name = 'fromGazePoint3d_az',
    marker_color = colors_idx[5],
    mode='markers',
    marker_size = 3,
    opacity = .5)

traces.append(fromGP3D_el)
traces.append(fromGP3D_az)


layout = dict(
    dragmode= 'pan',
    title='Time Series with Rangeslider',
    width=width,
    height=height,
    yaxis=dict(range=yLim, title='angular position (degrees)'),
    xaxis=dict(
        rangeslider=dict(visible=True))
)


fig = dict(data=traces, layout=layout)

iplot(fig)




Plotting from index: 1 to 7935
